<a href="https://colab.research.google.com/github/sclaudiobr/covid2019/blob/master/COVID19_Heatmap.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!pip install --upgrade folium
!pip install geobr

In [98]:
import pandas as pd
import numpy as np
import folium
from folium import plugins
import json
import geobr as br
print("Nova versão do Folium: ", folium.__version__)

Nova versão do Folium:  0.11.0


In [110]:
!wget https://data.brasil.io/dataset/covid19/caso.csv.gz

--2021-01-02 06:09:11--  https://data.brasil.io/dataset/covid19/caso.csv.gz
Resolving data.brasil.io (data.brasil.io)... 104.26.8.175, 172.67.71.45, 104.26.9.175, ...
Connecting to data.brasil.io (data.brasil.io)|104.26.8.175|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 13138737 (13M) [application/gzip]
Saving to: ‘caso.csv.gz’

caso.csv.gz         100%[===================>]  12.53M  4.80MB/s    in 2.6s    

2021-01-02 06:09:15 (4.80 MB/s) - ‘caso.csv.gz’ saved [13138737/13138737]



In [111]:
import requests
r =requests.get('https://data.brasil.io/dataset/covid19/caso.csv.gz', allow_redirects=True)
open('caso.csv.gz', 'wb').write(r.content)
df = pd.read_csv("caso.csv.gz", compression='gzip')
cidades = br.read_municipal_seat(year=2010)
df.head()

date state  ... confirmed_per_100k_inhabitants death_rate
0  2020-12-31    AC  ...                     4653.03476     0.0191
1  2020-12-30    AC  ...                     4623.40828     0.0192
2  2020-12-29    AC  ...                     4609.65712     0.0192
3  2020-12-28    AC  ...                     4584.83795     0.0192
4  2020-12-27    AC  ...                     4572.54016     0.0192

[5 rows x 13 columns]

In [112]:
# Aqui fazemos a troca de índice de cidades pelo códifo do IBGE
cidades = cidades.set_index('code_muni')
cidades.head()

name_muni code_state  ...  year                     geometry
code_muni                                    ...                                   
1100015.0  Alta Floresta D'oeste         11  ...  2010  POINT (-61.99982 -11.93554)
1100023.0              Ariquemes         11  ...  2010   POINT (-63.03327 -9.90846)
1100031.0                 Cabixi         11  ...  2010  POINT (-60.54431 -13.49976)
1100049.0                 Cacoal         11  ...  2010  POINT (-61.44294 -11.43387)
1100056.0             Cerejeiras         11  ...  2010  POINT (-60.81843 -13.19503)

[5 rows x 7 columns]

In [115]:
cities = df.loc[df.place_type == 'city',:]
cities.place_type.unique()

array(['city'], dtype=object)

In [116]:
cidades

name_muni code_state  ...  year                     geometry
code_muni                                    ...                                   
1100015.0  Alta Floresta D'oeste         11  ...  2010  POINT (-61.99982 -11.93554)
1100023.0              Ariquemes         11  ...  2010   POINT (-63.03327 -9.90846)
1100031.0                 Cabixi         11  ...  2010  POINT (-60.54431 -13.49976)
1100049.0                 Cacoal         11  ...  2010  POINT (-61.44294 -11.43387)
1100056.0             Cerejeiras         11  ...  2010  POINT (-60.81843 -13.19503)
...                          ...        ...  ...   ...                          ...
5222005.0             Vianópolis         52  ...  2010  POINT (-48.51347 -16.74208)
5222054.0         Vicentinópolis         52  ...  2010  POINT (-49.80724 -17.73266)
5222203.0               Vila Boa         52  ...  2010  POINT (-47.05736 -15.03489)
5222302.0          Vila Propício         52  ...  2010  POINT (-48.88242 -15.45463)
5300108.0               Brasília         53  ...  2010  POINT (-47.88791 -15.79409)

[5565 rows x 7 columns]

In [117]:
# juntar as duas bases de dados (IBGE cidades) come guardar na variável cities
cities = cities.join(cidades, on='city_ibge_code')

In [118]:
import geopandas as gpd
gdf = gpd.GeoDataFrame(cities, crs="EPSG:4326")
gdf['latitude'] = gdf.geometry.y
gdf['longitude'] = gdf.geometry.x
cities = gdf

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:2: FutureWarning: CRS mismatch between CRS of the passed geometries and 'crs'. Use 'GeoDataFrame.set_crs(crs, allow_override=True)' to overwrite CRS or 'GeoDataFrame.to_crs(crs)' to reproject geometries. CRS mismatch will raise an error in the future versions of GeoPandas.
  


In [119]:
# selecionar as colunas de interesse da tabela "cities", 
# geo_last são os ultimos registros da tabela para cada cidade
geo_last = cities.loc[cities.is_last==True,['city','latitude', 'longitude','state','confirmed','deaths']]
geo_last.head()

city   latitude  longitude state  confirmed  deaths
291     Acrelândia -10.073794 -67.052317    AC        563      12
564   Assis Brasil -10.942866 -69.563459    AC        762       9
804      Brasiléia -11.016411 -68.747943    AC       1298      22
1036        Bujari  -9.820020 -67.951859    AC        491       8
1299      Capixaba -10.569768 -67.673508    AC        305       8

In [120]:
#Quantidade de cidades com casos de covid-19
len(geo_last)

5589

In [121]:
#Quantidade de casos confirmados 
geo_last.confirmed.sum()

7534823

In [122]:
#Quantidade de mortes por covid-19
geo_last.deaths.sum()

192263

In [123]:
#Porcentagem de mortos sobre os casos confirmados
geo_last.deaths.sum()/geo_last.confirmed.sum()*100

2.5516591431543914

In [124]:
# verificar se todos os estados estão inseridos
len(geo_last.state.unique())

27

In [125]:
# Separando o conjunto de dados da interpolação
coordenadas = geo_last[['latitude','longitude','confirmed']]
#retirar as linhas que tiver dados faltando
coordenadas = coordenadas.dropna()
coordenadas.head()

latitude  longitude  confirmed
291  -10.073794 -67.052317        563
564  -10.942866 -69.563459        762
804  -11.016411 -68.747943       1298
1036  -9.820020 -67.951859        491
1299 -10.569768 -67.673508        305

In [126]:
baseMap = folium.Map(
    width = '100%',   height = '100%',
    location = [-15.77972, -47.92972], # <- Brasil
    zoom_start = 4
)

In [127]:
baseMap

In [128]:
baseMap = baseMap.add_child(plugins.HeatMap(coordenadas))

In [129]:
baseMap

In [130]:
# retirar dados faltantes
geo_last = geo_last.dropna()
geo_last.head(5)

city   latitude  longitude state  confirmed  deaths
291     Acrelândia -10.073794 -67.052317    AC        563      12
564   Assis Brasil -10.942866 -69.563459    AC        762       9
804      Brasiléia -11.016411 -68.747943    AC       1298      22
1036        Bujari  -9.820020 -67.951859    AC        491       8
1299      Capixaba -10.569768 -67.673508    AC        305       8

In [131]:
for i in range(0,len(geo_last)):
    folium.Circle(
        location = [geo_last.iloc[i]['latitude'], geo_last.iloc[i]['longitude']],
        color = '#00FF69',
        fill = '#00A1B3',
        tooltip = '<li><bold> CIDADE: '+ str(geo_last.iloc[i]['city']) + "</li></bold>" +
                 '<li><bold> ESTADO: '+ str(geo_last.iloc[i]['state']) +"</li></bold>" +
                 '<li><bold> CONFIRMADOS: '+ str(geo_last.iloc[i]['confirmed'])+"</li></bold>" +
                 '<li><bold> MORTES: '+ str(geo_last.iloc[i]['deaths']) + "</li></bold>" ,
        radius = (geo_last.iloc[i]['confirmed']**0.78)
                                            
    ).add_to(baseMap)
#baseMap

In [132]:
# importando logomarca e colocando no mapa
from folium.plugins import FloatImage
url = 'https://raw.githubusercontent.com/sclaudiobr/algoritmos-py/master/text43.png'
FloatImage(url,bottom=10,left=55).add_to(baseMap)
baseMap

In [133]:
baseMap.save('heatmap-cidade.html')